# **THU THẬP DỮ LIỆU**
## Ý tưởng 
    Nhóm muốn thu thập thông tin về các yếu tố ảnh hưởng đến giá nhà (Bao gồm: chung cư, nhà đất, ...) tại thành phố Hồ Chí Minh
    VD: Diện tích, số phòng ngủ, phòng tắm, ... và các tiện ích liên quan
## Thực hiện
    Nhóm đã tìm được trang web khá phù hợp để thu thập dữ liệu
    'https://rever.vn'
    

In [1]:
# IMPORT THƯ VIỆN
import numpy
from bs4 import BeautifulSoup
import urllib.request
from protego import Protego
import requests
from requests import Session
import lxml
import re
import pandas as pd
from time import sleep

In [2]:
# Khởi tạo phương thức get
s = Session()
headers = {'User-Agent': 'Mozilla/5.0 (X11; Linux x86_64) '\
                         'AppleWebKit/537.36 (KHTML, like Gecko) '\
                         'Chrome/75.0.3770.80 Safari/537.36'}
# Add headers
s.headers.update(headers)
# we can use s as we do requests
# s.get(...)


#### Kiểm tra robots.txt
    Dùng thư viện protego để kiểm tra việc thu thập dữ liệu của trang web này có vi phạm không?
    Kết quả trả về True có nghĩa là được phép.

In [3]:
# kiểm tra việc thu thập
base_url = 'https://rever.vn'

r = s.get(base_url + "/robots.txt")
rp = Protego.parse(r.text)
rp.can_fetch(base_url, "*")

True

In [4]:
# Thu thập số trang của phần mua nhà, lưu vào file csv
def get_number_of_pages(url):
    
    """
    Hàm thu thập tất cả trang web của phần mua nhà
    """
    req = s.get(url)
    bs = BeautifulSoup(req.text, 'lxml')
    url_last = bs.findAll('a', class_ = 'btnNext')
    result = re.sub(r'\D', "", url_last[0]['href'])    
    return int(result)


page_urls = set()
num_pages = get_number_of_pages('https://rever.vn/s/ho-chi-minh/mua')

for i in range(1, num_pages+1):
    page_urls.add('https://rever.vn/s/ho-chi-minh/mua?page=' + str(i) +'&search_mode=1')
    
list_page_urls = list(page_urls)
page_urls_df = pd.DataFrame({'URL' : list_page_urls})
page_urls_df.to_csv("PAGEs_urls.csv", sep = '\t')

# Tổng số trang
pages_df = pd.read_csv('PAGEs_urls.csv', sep = '\t')
pages_df.head()

356

In [5]:
def crawl_house_one_page(one_page_url):
    """
    Hàm thu thập tất cả url của các căn nhà trong 1 trang
    """
    req = s.get(one_page_url)
    bs = BeautifulSoup(req.text, 'lxml')
    list_pages = bs.findAll('div', class_ = 'group-grid__view')
        
    for house in list_pages:
        house_url = house.find('a')['href']
        house_url = base_url + house_url
        house_urls.add(house_url)

In [6]:
# Thu thập toàn bộ url và lưu vào file csv
house_urls = set()

for page in list_page_urls:
    crawl_house_one_page(page)
    
list_house_urls = list(house_urls)
house_urls_df = pd.DataFrame({'URL' : list_house_urls})
house_urls_df.to_csv("HOUSEs_urls.csv", sep = '\t')


In [7]:
houses_df = pd.read_csv('HOUSEs_urls.csv', sep = '\t')
len(houses_df)
houses_df.head()

Unnamed: 0                                                URL
0           0  https://rever.vn/mua/can-ho-vinhomes-golden-ri...
1           1  https://rever.vn/mua/can-ho-terra-royal-tang-c...
2           2  https://rever.vn/mua/ban-can-ho-new-city-thu-t...
3           3  https://rever.vn/mua/ban-can-ho-florita-2pn-di...
4           4  https://rever.vn/mua/ban-can-ho-one-verandah-t...

In [8]:
list_attribute = []
def get_info_house(one_house_url):
    '''
    get house's info from page
        input: house's url
        output: house's data
    '''
    data = {}

    req = s.get(one_house_url)
    bs = BeautifulSoup(req.text, 'lxml')
    left_house = bs.findAll('p', class_ = 'left')
    right_house = bs.findAll('p', class_ = 'right')
        
    list_attributes = []
    for attribute in left_house:
        list_attributes.append(attribute.text)
            
            
    list_values = []
    for value in right_house:
        if value.text != '':
            list_values.append(value.text)
        else:
            check = value['class']
            if any("close" in s for s in check):
                list_values.append('No')
            elif any("check" in s for s in check):
                list_values.append('Yes')
                    
                    
    for i in range(0, len(list_attributes)):
        data[list_attributes[i]] = list_values[i]

    return data

In [10]:
list_all_houses = []
i = 0
for house_url in list_house_urls:
    data_dict = {}
    data_dict = get_info_house(house_url)
    i = i + 1
    print(data_dict)
    print('\n', i )
    list_all_houses.append(data_dict)
    

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '76.8 m²', 'Diện tích sử dụng': '76.8 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Vinhomes Golden River', 'Tháp': 'The Luxury 6', 'Giá bán': '8.9 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '75 m²', 'Diện tích sử dụng': '70 m²', 'Tình hình nội thất': 'Không có nội thất', 'Dự án': 'Saigon South Residence', 'Giá bán': '2.8 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No', 'Cảm biến cháy': 'No', 'Tủ lạnh': 'No'

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Diện tích': '35 m²', 'Diện tích sử dụng': '33 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'The Sun Avenue', 'Tháp': 'Block 6', 'Giá bán': '1.7 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n ': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No'

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Diện tích': '55 m²', 'Diện tích sử dụng': '50 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Đảo Kim Cương - Diamond Island', 'Tháp': 'Maldives', 'Trạng thái': 'Chưa bàn giao', 'Giá bán': '4.8 tỷ', 'Thời gian bắt đầu bán': '06/11/2019', 'Ban công': 'Yes', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'Yes', 'Phòng giải trí': 'Yes', 'Chỗ đậu xe hơi': 'Yes', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'Yes', 'Góc làm việc': 'Yes', 'Nhà kho': 'Yes', 'Nuôi thú cưng': 'No', 'Gym': 'Yes', 'Bàn ghế phòng khách': 'Yes', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'Yes', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'Yes', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'Yes', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'N

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Diện tích': '47.5 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Dự án': 'Đảo Kim Cương - Diamond Island', 'Giá bán': '3.6 tỷ', 'Thời gian bắt đầu bán': '28/07/2019', 'Ban công': 'Yes', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'Yes', 'Hồ bơi riêng': 'Yes', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'Yes', 'Bàn ghế phòng khách': 'Yes', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'Yes', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'Yes', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'Yes', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No', 'Cảm biến cháy'

...

{'Loại hình': 'Nhà phố', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Số tầng': '2', 'Diện tích': '49.7 m²', 'Diện tích sử dụng': '92.7 m²', 'Tình hình nội thất': 'Không có nội thất', 'Loại chủ quyền': 'Sổ hồng', 'Giá bán': '3.9 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No', 'Cảm biến cháy': 'No', 'T

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '66.66 m²', 'Diện tích sử dụng': '66.66 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Q7 Saigon Riverside', 'Tháp': 'MERCURY', 'Trạng thái': 'Chưa bàn giao', 'Giá bán': '2.55 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang đi

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '3', 'Phòng tắm': '2', 'Số tầng': '22', 'Diện tích': '82 m²', 'Diện tích sử dụng': '75 m²', 'Tình hình nội thất': 'Không có nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Vinhomes Grand Park', 'Tháp': 'S1.02', 'Giá bán': '3.18 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No

{'Loại hình': 'Office-tel', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Diện tích': '45 m²', 'Diện tích sử dụng': '43 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'The Sun Avenue', 'Tháp': 'Block 3', 'Giá bán': '2.6 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'Yes', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'Yes', 'Máy hút mùi':

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Số tầng': '6', 'Diện tích': '71.3 m²', 'Diện tích sử dụng': '67.1 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Precia', 'Trạng thái': 'Chưa bàn giao', 'Giá bán': '4.07 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': '

In [13]:
len(list_all_houses)

7111

In [18]:
# all_houses_df = pd.DataFrame(list_all_houses)
all_houses_df = pd.DataFrame.from_dict(list_all_houses)
all_houses_df.shape


(7111, 123)

In [20]:
all_houses_df.to_csv("HOUSEs_info.csv", sep = '\t')
all_houses_df

Loại hình Phòng ngủ Phòng tắm Diện tích Diện tích sử dụng  \
0       Căn hộ         2         2   76.8 m²           76.8 m²   
1       Căn hộ         2         2     72 m²             72 m²   
2       Căn hộ         2         2     75 m²             75 m²   
3       Căn hộ         2         2  78.75 m²               NaN   
4       Căn hộ         2         2     73 m²               NaN   
...        ...       ...       ...       ...               ...   
7106    Căn hộ         2         2     81 m²             81 m²   
7107    Căn hộ         2         1   60.7 m²             55 m²   
7108       NaN       NaN       NaN        44               NaN   
7109    Căn hộ         2         2     70 m²             70 m²   
7110    Căn hộ         1         1     34 m²             30 m²   

     Tình hình nội thất Loại chủ quyền                   Dự án          Tháp  \
0       Đầy đủ nội thất     HĐ mua bán   Vinhomes Golden River  The Luxury 6   
1       Đầy đủ nội thất            NaN             Terra Royal           NaN   
2       Đầy đủ nội thất     HĐ mua bán  The New City Thủ Thiêm       Babylon   
3       Đầy đủ nội thất            NaN          Căn hộ Florita           NaN   
4     Không có nội thất            NaN            One Verandah           NaN   
...                 ...            ...                     ...           ...   
7106    Đầy đủ nội thất     HĐ mua bán           The Gold View        Tháp A   
7107    Đầy đủ nội thất            NaN         Grand Riverside           NaN   
7108                NaN        Sổ hồng                     NaN           NaN   
7109    Đầy đủ nội thất            NaN       Masteri Thảo Điền            T3   
7110  Không có nội thất     HĐ mua bán     Vinhomes Grand Park         S5.02   

      Giá bán  ... Căn hộ hạng sang Căn hộ view sông Đầy đủ vệ sinh Kệ bếp  \
0      8.9 tỷ  ...              NaN              NaN            NaN    NaN   
1      7.5 tỷ  ...              NaN              NaN            NaN    NaN   
2      4.5 tỷ  ...              NaN              NaN            NaN    NaN   
3     3.65 tỷ  ...              NaN              NaN            NaN    NaN   
4      6.1 tỷ  ...              NaN              NaN            NaN    NaN   
...       ...  ...              ...              ...            ...    ...   
7106     4 tỷ  ...              NaN              NaN            NaN    NaN   
7107  3.61 tỷ  ...              NaN              NaN            NaN    NaN   
7108      NaN  ...              NaN              NaN            NaN    NaN   
7109  4.38 tỷ  ...              NaN              NaN            NaN    NaN   
7110  1.47 tỷ  ...              NaN              NaN            NaN    NaN   

     Hoàn thiện cơ bản Hồ bơi tràn Khu tiệc nướng BBQ Vườn tiểu cảnh  \
0                  NaN         NaN                NaN            NaN   
1                  NaN         NaN                NaN            NaN   
2                  NaN         NaN                NaN            NaN   
3                  NaN         NaN                NaN            NaN   
4                  NaN         NaN                NaN            NaN   
...                ...         ...                ...            ...   
7106               NaN         NaN                NaN            NaN   
7107               NaN         NaN                NaN            NaN   
7108               NaN         NaN                NaN            NaN   
7109               NaN         NaN                NaN            NaN   
7110               NaN         NaN                NaN            NaN   

     khuôn viên đi dạo Khu vui chơi trẻ em  
0                  NaN                 NaN  
1                  NaN                 NaN  
2                  NaN                 NaN  
3                  NaN                 NaN  
4                  NaN                 NaN  
...                ...                 ...  
7106               NaN                 NaN  
7107               NaN                 NaN  
7108               NaN                 NaN  